In [21]:
# Imports
import sys
import os
import numpy as np
import pandas as pd
import keras
from keras import optimizers
from keras.models import Sequential
from keras.layers import Conv1D, MaxPooling1D, Flatten, Dense, Dropout, Activation
from tensorflow.keras.layers import BatchNormalization
from keras.callbacks import ModelCheckpoint
from keras.utils.np_utils import to_categorical
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split

from numpy import argmax
import seaborn as sns

from imp import reload

import matplotlib.pyplot as plt
%matplotlib inline
import csv
import scipy as sp
import getFeatures as gf
import mne

from pathlib import Path
%matplotlib inline
from time import time
from sklearn import metrics
import matplotlib.pyplot as plt

from sklearn import datasets, neighbors, linear_model, tree
from sklearn.decomposition import PCA
from sklearn.decomposition import PCA as RandomizedPCA
from sklearn.model_selection import train_test_split
# from sklearn.cross_validation import train_test_split
from sklearn.metrics import classification_report, confusion_matrix

#1-KNN
from sklearn.neighbors import KNeighborsClassifier
#2-RandomForest
from sklearn.ensemble import RandomForestClassifier
#3-SVM
from sklearn import datasets, svm
#4-DecisionTree
from sklearn import tree
#5-LDA
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
#6-GaussianNB
from sklearn.naive_bayes import GaussianNB
#7-MLP
from sklearn.neural_network import MLPClassifier

In [22]:
def csv_to_mne_raw(csv_file_path):
  #read the csv file into a pandas dataframe
  df = pd.read_csv(csv_file_path)

  #get the starting 10 columns corresponding to the 8 channels and the index data
  df1 = df.iloc[:,0:10]

  #also keep the timestamp, Cognitive Workload and Anxiety column
  df1['Timestamp'] = pd.to_datetime(df[' Timestamp (Formatted)'])
  df1['Cognitive Workload'] = df['Cognitive_Wokload']
  df1['Anxiety'] = df['Anxiety']

  #reindex the columns
  df1 = df1.reindex(columns=[' EXG Channel 0', ' EXG Channel 1', ' EXG Channel 2',
                            ' EXG Channel 3', ' EXG Channel 4', ' EXG Channel 5', 
                            ' EXG Channel 6', ' EXG Channel 7', 'Changed Sample Index',
                            'Sample Index','Cognitive Workload','Anxiety','Timestamp'])


  #drop the sample index column
  df1 = df1.drop(['Sample Index'], axis=1)

  #rename the channels
  df1 = df1.rename(columns={' EXG Channel 0': 'eeg1', ' EXG Channel 1': 'eeg2',
                            ' EXG Channel 2': 'eeg3', ' EXG Channel 3': 'eeg4',
                              ' EXG Channel 4': 'eeg5', ' EXG Channel 5': 'eeg6',
                              ' EXG Channel 6': 'eeg7', ' EXG Channel 7': 'eeg8',
                              'Changed Sample Index':'Index'})


  #convert dataframe to numpy array
  data = df1[['eeg1','eeg2','eeg3','eeg4','eeg5','eeg6','eeg7','eeg8']].to_numpy()
  # data = df1.to_numpy()

  #convert the data to float32
  data = data.astype('float32')

  # Scaling Data with the scale factor S = (4500000)/4/(2**23-1)
  data = data*4500000/4/(2**23-1)

  #get transpose of the data
  data = data.T

  # Create some metadata
  n_channels = 8
  sampling_freq = 250  # in Hertz
  ch_types = ['eeg'] * n_channels
  ch_names = ['eeg1', 'eeg2', 'eeg3', 'eeg4', 'eeg5', 'eeg6', 'eeg7', 'eeg8']
  info = mne.create_info( ch_names=ch_names, sfreq=sampling_freq,ch_types=ch_types)
  # print(info)
  raw = mne.io.RawArray(data, info)
  return raw,df1.iloc[0]['Cognitive Workload'] 

In [23]:
features = ['Coeffiecient of Variation','Mean of Vertex to Vertex Slope','Variance of Vertex to Vertex Slope',
         'Hjorth_Activity','Hjorth_Mobility','Hjorth_Complexity',
         'Kurtosis','2nd Difference Mean','2nd Difference Max',
         'Skewness','1st Difference Mean','1st Difference Max',
         'FFT Delta MaxPower','FFT Theta MaxPower','FFT Alpha MaxPower','FFT Beta MaxPower','Delta/Theta','Delta/Alpha','Theta/Alpha','(Delta+Theta)/Alpha',
         '1Wavelet Approximate Mean','Wavelet Approximate Std Deviation','Wavelet Approximate Energy','Wavelet Detailed Mean','Wavelet Detailed Std Deviation','Wavelet Detailed Energy','Wavelet Approximate Entropy','Wavelet Detailed Entropy',
         '2Wavelet Approximate Mean','Wavelet Approximate Std Deviation','Wavelet Approximate Energy','Wavelet Detailed Mean','Wavelet Detailed Std Deviation','Wavelet Detailed Energy','Wavelet Approximate Entropy','Wavelet Detailed Entropy',
         '3Wavelet Approximate Mean','Wavelet Approximate Std Deviation','Wavelet Approximate Energy','Wavelet Detailed Mean','Wavelet Detailed Std Deviation','Wavelet Detailed Energy','Wavelet Approximate Entropy','Wavelet Detailed Entropy',
         '4Wavelet Approximate Mean','Wavelet Approximate Std Deviation','Wavelet Approximate Energy','Wavelet Detailed Mean','Wavelet Detailed Std Deviation','Wavelet Detailed Energy','Wavelet Approximate Entropy','Wavelet Detailed Entropy',
         '5Wavelet Approximate Mean','Wavelet Approximate Std Deviation','Wavelet Approximate Energy','Wavelet Detailed Mean','Wavelet Detailed Std Deviation','Wavelet Detailed Energy','Wavelet Approximate Entropy','Wavelet Detailed Entropy',
         '6Wavelet Approximate Mean','Wavelet Approximate Std Deviation','Wavelet Approximate Energy','Wavelet Detailed Mean','Wavelet Detailed Std Deviation','Wavelet Detailed Energy','Wavelet Approximate Entropy','Wavelet Detailed Entropy',
         '7Wavelet Approximate Mean','Wavelet Approximate Std Deviation','Wavelet Approximate Energy','Wavelet Detailed Mean','Wavelet Detailed Std Deviation','Wavelet Detailed Energy','Wavelet Approximate Entropy','Wavelet Detailed Entropy',
         '8Wavelet Approximate Mean','Wavelet Approximate Std Deviation','Wavelet Approximate Energy','Wavelet Detailed Mean','Wavelet Detailed Std Deviation','Wavelet Detailed Energy','Wavelet Approximate Entropy','Wavelet Detailed Entropy',
         'AR1','AR2','AR3','AR4','AR5','AR6','AR7','AR8','AR9','AR10','AR11','AR12','AR13','AR14','AR15','AR16','AR17','AR18',
         'AR19','AR20','AR21','AR22','AR23','AR24']

In [39]:
def createFeatures(files,data_dir,flag):

    if(flag==0):
        features_csv_file = 'features_train.csv'
    else:
        features_csv_file = 'features_test.csv'
    features_csv_file_path = data_dir/features_csv_file
    #delete the file if it exists
    if os.path.exists(features_csv_file_path):
        os.remove(features_csv_file_path)


    with open(features_csv_file_path, "a",newline='') as output:
        writer = csv.writer(output, lineterminator='\n')
        writer.writerow(features)
        for counter in range(len(files)):
            data_path = files[counter]
            print(data_path)
            # read the csv file and get a mne raw object
            data,label = csv_to_mne_raw(data_path)
            # get the data in ndarray
            raw_data = data.get_data()

            #apply a band pass filter of 1-40Hz
            filtered_data = mne.filter.filter_data(raw_data,sfreq=250,l_freq=1,h_freq=40)

            # sigbufs = [l for l in filtered_data]
            sigbufs = [l for l in raw_data]
            sigbufs = np.array(sigbufs)
            sigbufs = sigbufs.transpose()
            sigbufs = sigbufs.astype(float)

            print(sigbufs.shape)
            # continue

            #get the features
            for i in np.arange(0,185):
                temp_features = []
                epoch = sigbufs[i*250:(i+1)*250,:]
                if (len(epoch)==0 or len(epoch[0]) == 0):
                    break
            
                #Coeffeicient of Variation
                temp_features.append(gf.coeff_var(epoch))

                #Mean of Vertex to Vertex Slope
                temp_features.append(gf.slope_mean(epoch))
                
                #Variance of Vertex to Vertex Slope
                temp_features.append(gf.slope_var(epoch))

                #Hjorth Parameters
                feature_list = gf.hjorth(epoch)
                for feat in feature_list:
                    temp_features.append(feat)
                
                #Kurtosis
                temp_features.append(gf.kurtosis(epoch))

                #Second Difference Mean
                temp_features.append(gf.secDiffMean(epoch))

                #Second Difference Max
                temp_features.append(gf.secDiffMax(epoch))
                
                #Skewness
                temp_features.append(gf.skewness(epoch))
    
                #First Difference Mean
                temp_features.append(gf.first_diff_mean(epoch))

                #First Difference Max
                temp_features.append(gf.first_diff_max(epoch))

                # print(type(epoch))
                epoch_t = epoch.transpose()
                #FFT Max Power - Delta, Theta, Alpha & Beta Band!
                # feature_list  =  maxPwelch(epoch,128)            
                feature_list  =  gf.maxPwelch(epoch_t,250)            
                for feat in feature_list:
                    temp_features.append(feat)
                #FFT Frequency Ratios
                temp_features.append(feature_list[0]/feature_list[1])
                temp_features.append(feature_list[0]/feature_list[2])
                temp_features.append(feature_list[1]/feature_list[3])
                temp_features.append((feature_list[0] + feature_list[1])/feature_list[2])
                
                #Wavelet Fetures!      lineterminator
                feature_list = gf.wavelet_features(epoch,8)
                for feat in feature_list:
                    temp_features.append(feat)
                        
                #Autoregressive model Coefficients
                feature_list = gf.autogressiveModelParametersBurg(epoch)
                for feat in feature_list:
                    temp_features.append(feat.real)

                temp_features.append(label)
                writer.writerow(temp_features)

    if(flag==0):
        r = csv.reader(open('features_train.csv'))
    else:
        r = csv.reader(open('features_test.csv')) 
        
    lines = [l for l in r]
    for i in range(len(lines[1])-1):  
        columns = []
        for j in range(1,len(lines)):
            columns.append(float(lines[j][i]))
        mean = np.mean(columns,axis = 0)
        #print('\nMean = ',mean)
        std_dev  = np.std(columns,axis = 0)
        #print('\nSTD Deviation = ',std_dev)
        for j in range(1,len(lines)):
            lines[j][i] = (float(lines[j][i])-mean)/std_dev

    norm_file = ''
    if(flag==0):
        norm_file = 'Normalizedfeatures_train.csv'
    else:
        norm_file = 'Normalizedfeatures_test.csv'
    writer = csv.writer(open(norm_file, 'w'))
    writer.writerows(lines)
    print('Done!')

        

In [34]:
files = []
data_dir = Path.cwd()
user_data_path = data_dir/'User_data'
for user in os.listdir(user_data_path):
    for session in os.listdir(user_data_path/user):
        for file in os.listdir(user_data_path/user/session):
            if file.endswith('.csv') and not file.endswith('_HEP.csv'):
                path = user_data_path/user/session/file
                path = str(path)
                files.append(path)

In [26]:
def KNN(X_train, X_test, y_train, y_test):
    # KNN
    model = neighbors.KNeighborsClassifier(n_neighbors = 3)
    model.fit(X_train, y_train)
    model.fit(X_train, y_train)
    y_test_pred = model.predict(X_test)
    return metrics.accuracy_score(y_test, y_test_pred, normalize=True, sample_weight=None)

In [27]:
def RandomForest(X_train, X_test, y_train, y_test):
    model = RandomForestClassifier(n_estimators=100, n_jobs=4)
    model.fit(X_train, y_train)
    model.fit(X_train, y_train)
    y_test_pred = model.predict(X_test)
    return metrics.accuracy_score(y_test, y_test_pred, normalize=True, sample_weight=None)

In [28]:
def SVM(X_train, X_test, y_train, y_test):
    def evaluate_on_test_data(model=None):
        predictions = model.predict(X_test)
        correct_classifications = 0
        for i in range(len(y_test)):
            if predictions[i] == y_test[i]:
                correct_classifications += 1
        accuracy = 100*correct_classifications/len(y_test) #Accuracy as a percentage
        return accuracy

    kernels = ('rbf')
    model = svm.SVC(kernel=kernel)
    model.fit(X_train, y_train)
    acc = evaluate_on_test_data(model)
    return acc

In [29]:
def MLP(X_train, X_test, y_train, y_test):
    model = MLPClassifier(hidden_layer_sizes=(25,), random_state=1)
    model.fit(X_train, y_train)
    model.fit(X_train, y_train)
    y_test_pred = model.predict(X_test)
    metrics.accuracy_score(y_test, y_test_pred, normalize=True, sample_weight=None)

In [30]:
#5-DecisionTree
def DecisionTree(X_train, X_test, y_train, y_test):
    model = tree.DecisionTreeClassifier()
    model.fit(X_train, y_train)
    model.fit(X_train, y_train)
    y_test_pred = model.predict(X_test)
    metrics.accuracy_score(y_test, y_test_pred, normalize=True, sample_weight=None)

In [31]:
def LDA(X_train, X_test, y_train, y_test):
    model = LinearDiscriminantAnalysis(solver='lsqr', shrinkage=None) #shrinkage='auto'
    model.fit(X_train, y_train)
    model.fit(X_train, y_train)
    y_test_pred = model.predict(X_test)
    metrics.accuracy_score(y_test, y_test_pred, normalize=True, sample_weight=None)

In [32]:
def result_preprocesing(flag):
    file = ''
    if flag == 0:
        file = 'Normalizedfeatures_train.csv'
    else:
        file = 'Normalizedfeatures_test.csv'
        
    df = pd.read_csv(file)
    df.drop('Mean of Vertex to Vertex Slope', axis = 1, inplace = True)
    df.drop('Coeffiecient of Variation', axis = 1, inplace = True)
    df.to_csv(file)
    f = open(file)
    attributes=f.readline()
    X = []
    y = []
    for line in f:
        line = line.rstrip().split(',')
        print(line)
        l = [float(i) for i in line]
        X.append(l[:-1])
        y.append(l[-1])
        
    X = np.asarray(X)
    y = np.asarray(y)
    return X,y
    

In [40]:
for i,item in enumerate(files):
    #create a new list not having the ith item
    print(files)
    train = files[:i] + files[i+1:]
    test = files[i]
    createFeatures(train,data_dir,0)
    result_preprocesing(0)
    X_train, y_train = result_preprocesing(0)
    createFeatures(test,data_dir,1)
    result_preprocesing(1)
    X_test, y_test = result_preprocesing(1)

    accuracy_dict ={}
    accuracy_dict['KNN'] = KNN(X_train, X_test, y_train, y_test)
    accuracy_dict['RandomForest'] = RandomForest(X_train, X_test, y_train, y_test)
    accuracy_dict['SVM'] = SVM(X_train, X_test, y_train, y_test)
    accuracy_dict['MLP'] = MLP(X_train, X_test, y_train, y_test)
    accuracy_dict['DecisionTree'] = DecisionTree(X_train, X_test, y_train, y_test)
    accuracy_dict['LDA'] = LDA(X_train, X_test, y_train, y_test)

    #find the best model
    best_model = max(accuracy_dict, key=accuracy_dict.get)
    print('Best model is ', best_model, 'with accuracy', accuracy_dict[best_model])
    break
    
    

['/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12352/session_1/12352_session_1_02-04-2023_21-51.csv', '/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12352/session_2/12352_session_2_02-04-2023_21-55.csv', '/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12353/session_1/12353_session_1_02-04-2023_22-07.csv', '/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12353/session_2/12353_session_2_02-04-2023_22-12.csv', '/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12354/session_1/12354_session_1_03-04-2023_23-02.csv', '/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12354/session_2/12354_session_2_03-04-2023_23-06.csv', '/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12350/session_1/12350_session_1_01-04-2023_15-50.csv', '/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12350/session_2/12350_session_2_01-04-2023_15-57.csv', '/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12351/session_1/12351_session_1_01-04-2023_16-44.csv', '/home/mt1/21CS60R01/OpenBCI_DataAnl

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:    0.0s finished
/home/mt1/21CS60R01/anaconda3/envs/OpenBCI/lib/python3.11/site-packages/scipy/signal/_spectral_py.py:2014: UserWarning: nperseg = 256 is greater than input length  = 250, using nperseg = 250
  warnings.warn('nperseg = {0:d} is greater than input length '


/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12353/session_1/12353_session_1_02-04-2023_22-07.csv
Creating RawArray with float64 data, n_channels=8, n_times=46250
    Range : 0 ... 46249 =      0.000 ...   184.996 secs
Ready.
Setting up band-pass filter from 1 - 40 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 1.00
- Lower transition bandwidth: 1.00 Hz (-6 dB cutoff frequency: 0.50 Hz)
- Upper passband edge: 40.00 Hz
- Upper transition bandwidth: 10.00 Hz (-6 dB cutoff frequency: 45.00 Hz)
- Filter length: 825 samples (3.300 sec)

(46250, 8)


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:    0.0s finished
/home/mt1/21CS60R01/anaconda3/envs/OpenBCI/lib/python3.11/site-packages/scipy/signal/_spectral_py.py:2014: UserWarning: nperseg = 256 is greater than input length  = 250, using nperseg = 250
  warnings.warn('nperseg = {0:d} is greater than input length '


/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12353/session_2/12353_session_2_02-04-2023_22-12.csv
Creating RawArray with float64 data, n_channels=8, n_times=46250
    Range : 0 ... 46249 =      0.000 ...   184.996 secs
Ready.
Setting up band-pass filter from 1 - 40 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 1.00
- Lower transition bandwidth: 1.00 Hz (-6 dB cutoff frequency: 0.50 Hz)
- Upper passband edge: 40.00 Hz
- Upper transition bandwidth: 10.00 Hz (-6 dB cutoff frequency: 45.00 Hz)
- Filter length: 825 samples (3.300 sec)

(46250, 8)


...

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:    0.0s finished
/home/mt1/21CS60R01/anaconda3/envs/OpenBCI/lib/python3.11/site-packages/scipy/signal/_spectral_py.py:2014: UserWarning: nperseg = 256 is greater than input length  = 250, using nperseg = 250
  warnings.warn('nperseg = {0:d} is greater than input length '


/home/mt1/21CS60R01/OpenBCI_DataAnlaysis/User_data/12348/session_2/12348_session_2_23-03-2023_23-17.csv
Creating RawArray with float64 data, n_channels=8, n_times=46250
    Range : 0 ... 46249 =      0.000 ...   184.996 secs
Ready.
Setting up band-pass filter from 1 - 40 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 1.00
- Lower transition bandwidth: 1.00 Hz (-6 dB cutoff frequency: 0.50 Hz)
- Upper passband edge: 40.00 Hz
- Upper transition bandwidth: 10.00 Hz (-6 dB cutoff frequency: 45.00 Hz)
- Filter length: 825 samples (3.300 sec)

(46250, 8)


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:    0.0s finished
/home/mt1/21CS60R01/anaconda3/envs/OpenBCI/lib/python3.11/site-packages/scipy/signal/_spectral_py.py:2014: UserWarning: nperseg = 256 is greater than input length  = 250, using nperseg = 250
  warnings.warn('nperseg = {0:d} is greater than input length '


Done!
['0.2470693952089127', '-0.3194528169257235', '-1.042293376234132', '1.5049395201027735', '-0.1040918537474221', '-0.3129261792745396', '-0.7316384127622909', '-0.5237712755852524', '-0.2797392069394071', '-0.2511514870256311', '-0.1768499112272737', '-0.4585717953620025', '-0.2830620457116823', '-0.1679020530295152', '-0.3007248850693278', '-0.2694106755466964', '0.082629785632338', '-0.2510863468050921', '-0.0905636681250069', '-0.1337091380015792', '-0.0847908410702748', '-0.1363993952757112', '-0.319052138687697', '-0.3360214633431019', '-0.3363287994773477', '-0.0978334213853469', '-0.0927440823458562', '-0.1336424275145268', '-0.0834115882457043', '-0.1360685701413955', '-0.3189519090505778', '-0.3360035255715212', '-0.3363140326969686', '-0.096518365011673', '-0.0847985170010432', '-0.1334581308594078', '-0.0884321725640525', '-0.1370761716547868', '-0.3190770534509018', '-0.3360280220280416', '-0.3363316388870753', '-0.1013057517450583', '-0.0782747878954014', '-0.1334936

TypeError: result_preprocesing() missing 1 required positional argument: 'flag'